In [1]:
import numpy as np
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
from scipy.spatial import distance
sns.set(style="whitegrid")
import gensim
import jieba
from tqdm import tqdm
from gensim.models.ldamodel import LdaModel

C:\Users\gaowenxin95\AppData\Roaming\Python\Python37\site-packages\statsmodels\tools\_testing.py:19: FutureWarning: pandas.util.testing is deprecated. Use the functions in the public API at pandas.testing instead.
  import pandas.util.testing as tm


In [2]:
from pyecharts.charts import Bar, Tab
from pyecharts import options as opts

In [3]:
import gc, functools,time
import pickle, re
import random
from typing import List
from pprint import pprint

In [4]:
stopwords = open('../data/cn_stopwords.txt',encoding='utf-8').read().split()
stopwords = frozenset(stopwords)
print(len(stopwords))

746


In [5]:
dataset = pd.read_csv('../data/s1000.csv',encoding='utf-8')
dataset.head()

time    none catagory  \
0  1951.08.15     4.0      NaN   
1  1982.04.24     7.0      NaN   
2  2012.12.25  2012.0     经济新闻   
3  1962.07.10     3.0      NaN   
4  1976.11.17     5.0      NaN   

                                               title  \
0                      全国各地签名拥护缔结和平公约投票反对美国武装日本人数统计表   
1               我国和各国代表在联大紧急特别会议上谴责以色列新罪行　支持巴勒斯坦人民斗争   
2                              营造安全可信的网络空间（关注网络信息保护）   
3      第十五届世界体操锦标赛闭幕各项比赛的前三名授奖仪式分别举行于烈烽获鞍马第三名赢得锦标赛奖章   
4  日本中国归还者联络会（正统）发表哀悼毛主席的声明毛主席激励世界人民反帝反霸斗争藤田会长热情庆...   

                                             content  
0  编者按：兹将全国拥护缔结和平公约签名及反对武装日本投票运动的最后结果按地区公布如下。这里发表...  
1  谴责以色列新罪行　支持巴勒斯坦人民斗争新华社联合国4月22日电中国代表团团长、中国常驻联合国...  
2  　　本报记者张洋　　通过网络立法，授权权威第三方电子认证机构对相关网站及其内容的真实性实施身...  
3  各项比赛的前三名授奖仪式分别举行于烈烽获鞍马第三名赢得锦标赛奖章新华社布拉格8日电　第十五届...  
4  毛主席激励世界人民反帝反霸斗争藤田会长热情庆贺华主席为首的中共中央粉碎“四人帮”的伟大胜利新...

In [6]:
df=dataset['content']


In [36]:
from sklearn.model_selection import train_test_split

In [37]:
df_train, df_test = train_test_split(df, test_size=0.3, random_state=45)

## 清洗

In [7]:
def seg_words(text):
    #去掉不在(所有中文、大小写字母、数字)中的非法字符
    regex = re.compile(r'[^\u4e00-\u9fa5]')
    text = regex.sub('', text) # 将非法字符用‘ ’替代
    text = text.strip() # 去掉前后的空格
    word_list = jieba.cut(text, cut_all= False)
    return word_list

In [38]:
train = df_train.apply(lambda x: " ".join(seg_words(str(x))))
test = df_test.apply(lambda x: " ".join(seg_words(str(x))))

In [9]:
train.head()

0    编者按 兹将 全国 拥护 缔结 和平 公约 签名 及 反对 武装 日本 投票 运动 的 最后...
1    谴责 以色列 新 罪行 支持 巴勒斯坦 人民 斗争 新华社 联合国 月 日电 中国 代表团 ...
2    本报记者 张洋 通过 网络 立法 授权 权威 第三方 电子 认证 机构 对 相关 网站 及其...
3    各项 比赛 的 前三名 授奖仪式 分别 举行 于烈 烽获 鞍马 第三名 赢得 锦标赛 奖章 ...
4    毛主席 激励 世界 人民 反帝 反霸 斗争 藤田 会长 热情 庆贺 华 主席 为首 的 中共...
Name: content, dtype: object

## 去停用词

In [39]:

#将文档中可能存在的西文字符小写化，按空格进行拆分，且去停用词
train_texts = [[word for word in document.lower().split() if word not in stopwords]
         for document in train]

test_texts = [[word for word in document.lower().split() if word not in stopwords]
         for document in test]

In [41]:
train_texts[0:1]

[['是兆雄',
  '日本',
  '东京',
  '三田',
  '一幢',
  '掩映',
  '绿荫',
  '之中',
  '高层建筑',
  '新一代',
  '计算机',
  '技术开发',
  '研究所',
  '拥有',
  '渕',
  '一博',
  '所长',
  '为首',
  '四十余名',
  '专家',
  '研究',
  '人员',
  '承担',
  '研究',
  '领导',
  '研制',
  '第五代',
  '计算机',
  '艰巨',
  '任务',
  '早',
  '一九七九年',
  '日本',
  '通产省',
  '授意',
  '成立',
  '新一代',
  '计算机',
  '调查',
  '委员会',
  '一年',
  '考察',
  '研究',
  '提出',
  '新一代',
  '计算机',
  '概念',
  '一九八',
  '年',
  '东京',
  '召开',
  '新一代',
  '计算机',
  '国际',
  '讨论会',
  '一九八一年',
  '十月',
  '日本',
  '正式',
  '宣布',
  '研制',
  '第五代',
  '计算机',
  '一九八二年',
  '四月',
  '通产省',
  '召集',
  '全国',
  '从事',
  '电子计算机',
  '生产',
  '研究',
  '教学',
  '各大',
  '公司',
  '大学',
  '科研单位',
  '制定',
  '一项',
  '为期',
  '十年',
  '一九八',
  '二至',
  '一九九',
  '第五代',
  '计算机技术',
  '开发计划',
  '总',
  '投资',
  '一千',
  '亿日元',
  '第五代',
  '计算机技术',
  '开发计划',
  '主要',
  '内容',
  '包括',
  '开发',
  '解决问题',
  '推断',
  '知识',
  '基础',
  '管理',
  '智能',
  '接口',
  '计算机',
  '三大',
  '功能',
  '达到',
  '这一',
  '目标',
  '新一代',
  '计算机',
  '技术开发',
  '研究所',
  '决心',
  '解决',
  '基本'

## 计算词频


In [42]:
from collections import defaultdict
train_frequency = defaultdict(int)
for text in train_texts:
    for token in text:
        train_frequency[token] += 1

In [43]:
from collections import defaultdict
test_frequency = defaultdict(int)
for text in train_texts:
    for token in text:
        test_frequency[token] += 1

# 仅保留词频数高于1的词汇


In [46]:
train_processed_corpus = [[token for token in text if train_frequency[token] > 1] for text in train_texts]
train_processed_corpus[0]

['日本',
 '东京',
 '三田',
 '掩映',
 '之中',
 '高层建筑',
 '新一代',
 '计算机',
 '技术开发',
 '研究所',
 '拥有',
 '所长',
 '为首',
 '四十余名',
 '专家',
 '研究',
 '人员',
 '承担',
 '研究',
 '领导',
 '研制',
 '第五代',
 '计算机',
 '艰巨',
 '任务',
 '早',
 '一九七九年',
 '日本',
 '通产省',
 '授意',
 '成立',
 '新一代',
 '计算机',
 '调查',
 '委员会',
 '一年',
 '考察',
 '研究',
 '提出',
 '新一代',
 '计算机',
 '概念',
 '一九八',
 '年',
 '东京',
 '召开',
 '新一代',
 '计算机',
 '国际',
 '讨论会',
 '一九八一年',
 '十月',
 '日本',
 '正式',
 '宣布',
 '研制',
 '第五代',
 '计算机',
 '四月',
 '通产省',
 '召集',
 '全国',
 '从事',
 '电子计算机',
 '生产',
 '研究',
 '教学',
 '各大',
 '公司',
 '大学',
 '科研单位',
 '制定',
 '一项',
 '为期',
 '十年',
 '一九八',
 '二至',
 '第五代',
 '计算机技术',
 '开发计划',
 '总',
 '投资',
 '一千',
 '亿日元',
 '第五代',
 '计算机技术',
 '开发计划',
 '主要',
 '内容',
 '包括',
 '开发',
 '解决问题',
 '推断',
 '知识',
 '基础',
 '管理',
 '智能',
 '计算机',
 '三大',
 '功能',
 '达到',
 '这一',
 '目标',
 '新一代',
 '计算机',
 '技术开发',
 '研究所',
 '决心',
 '解决',
 '基本',
 '应用',
 '系统',
 '基本',
 '计算机',
 '新',
 '体制',
 '共计',
 '二十六',
 '项',
 '关键技术',
 '问题',
 '领域',
 '推进',
 '国际',
 '协作',
 '宗旨',
 '派遣',
 '研究',
 '人员',
 '国外',
 '学习',
 '取经',
 '欢迎',
 '邀请',
 '外国',

In [47]:
test_processed_corpus = [[token for token in text if test_frequency[token] > 1] for text in test_texts]
test_processed_corpus[0]

['本报记者',
 '李长云',
 '坐',
 '为数不多',
 '观众',
 '称得上',
 '真正',
 '球迷',
 '接触',
 '大都',
 '流露出',
 '中国女排',
 '夺冠',
 '担忧',
 '观战',
 '记者',
 '中国女排',
 '亚洲',
 '实力',
 '以往',
 '坚强',
 '这是',
 '事实',
 '中国女排',
 '毕竟',
 '亚洲',
 '强队',
 '去年',
 '奥运会',
 '排名',
 '日本队',
 '之后',
 '今年',
 '四月',
 '调整',
 '不久前',
 '世界',
 '女排',
 '联赛',
 '击败',
 '劲旅',
 '获得',
 '亚军',
 '亚洲',
 '强队',
 '比较',
 '至少',
 '身高',
 '网上',
 '实力',
 '方面',
 '占有',
 '一定',
 '优势',
 '对手',
 '差',
 '中国女排',
 '夺取',
 '第七届',
 '亚洲',
 '女排',
 '赛',
 '冠军',
 '强有力',
 '保证',
 '调整',
 '中国女排',
 '年轻',
 '队员',
 '决心',
 '理由',
 '相信',
 '中国女排',
 '克服',
 '眼前',
 '暂时',
 '遇到',
 '困难',
 '争得',
 '参加',
 '明年',
 '世界',
 '锦标赛',
 '资格',
 '本报',
 '上海',
 '七月',
 '二十四日',
 '电']

## 将语料库中的每个词汇与唯一的整数ID相关联

python中的字典对象, 其Key是字典中的词，其Val是词对应的唯一数值型ID
构造方法，因此把每个词变成字典方便查找

In [14]:
from gensim import corpora

dictionary = corpora.Dictionary(processed_corpus)
print(dictionary)

Dictionary(25459 unique tokens: ['七月', '会', '全国', '公布', '公约']...)


In [15]:
print(dictionary.token2id)

{'七月': 0, '会': 1, '全国': 2, '公布': 3, '公约': 4, '兹将': 5, '十八': 6, '反对': 7, '发表': 8, '和平': 9, '图表': 10, '地区': 11, '增加': 12, '总结': 13, '投票': 14, '拥护': 15, '数字': 16, '日本': 17, '最后': 18, '武装': 19, '略有': 20, '签名': 21, '缔结': 22, '编者按': 23, '运动': 24, '附': 25, '一个': 26, '一次': 27, '不结盟': 28, '两个': 29, '严厉': 30, '中': 31, '中东地区': 32, '中东问题': 33, '中国': 34, '中国政府': 35, '主权': 36, '争取': 37, '事件': 38, '二十一日': 39, '人民': 40, '今天': 41, '今年': 42, '代表': 43, '代表团': 44, '以色列': 45, '会议': 46, '传真照片': 47, '侵略': 48, '停止': 49, '先后': 50, '全面': 51, '公正': 52, '共同愿望': 53, '内容': 54, '决议': 55, '凌青': 56, '出动': 57, '切实': 58, '制裁': 59, '制造': 60, '加沙': 61, '加紧': 62, '加纳': 63, '努力': 64, '包括': 65, '十': 66, '南部': 67, '占领': 68, '卫生部长': 69, '印度尼西亚': 70, '参加': 71, '反抗': 72, '反映': 73, '发': 74, '发言': 75, '叙利亚': 76, '另据': 77, '合法': 78, '否决': 79, '哈桑': 80, '唯一': 81, '嚣张': 82, '四月': 83, '团长': 84, '国': 85, '国家': 86, '国际': 87, '国际形势': 88, '图为': 89, '在内': 90, '地带': 91, '坚决': 92, '基地': 93, '墨西哥': 94, '大批': 95, '奈克': 96, '安全': 97, '安哥拉': 98,

## 使用dictionary的doc2bow方法为这些语句创建词袋表示，该方法返回词汇计数的稀疏表示：

In [53]:
bow_corpus = [dictionary.doc2bow(text) for text in processed_corpus]
corpora.MmCorpus.serialize('../data/train_corpuse.mm', bow_corpus)
bow_corpus

[[(0, 1),
  (1, 1),
  (2, 1),
  (3, 1),
  (4, 1),
  (5, 1),
  (6, 1),
  (7, 1),
  (8, 2),
  (9, 1),
  (10, 1),
  (11, 1),
  (12, 1),
  (13, 1),
  (14, 2),
  (15, 1),
  (16, 1),
  (17, 2),
  (18, 2),
  (19, 1),
  (20, 1),
  (21, 2),
  (22, 1),
  (23, 1),
  (24, 1),
  (25, 1)],
 [(4, 1),
  (7, 1),
  (9, 2),
  (17, 1),
  (26, 2),
  (27, 1),
  (28, 1),
  (29, 2),
  (30, 1),
  (31, 1),
  (32, 1),
  (33, 2),
  (34, 2),
  (35, 1),
  (36, 1),
  (37, 1),
  (38, 1),
  (39, 1),
  (40, 8),
  (41, 1),
  (42, 1),
  (43, 10),
  (44, 1),
  (45, 13),
  (46, 2),
  (47, 1),
  (48, 5),
  (49, 1),
  (50, 2),
  (51, 1),
  (52, 2),
  (53, 1),
  (54, 1),
  (55, 2),
  (56, 5),
  (57, 2),
  (58, 1),
  (59, 1),
  (60, 1),
  (61, 2),
  (62, 1),
  (63, 1),
  (64, 1),
  (65, 3),
  (66, 1),
  (67, 1),
  (68, 3),
  (69, 1),
  (70, 1),
  (71, 1),
  (72, 1),
  (73, 1),
  (74, 1),
  (75, 2),
  (76, 2),
  (77, 1),
  (78, 1),
  (79, 1),
  (80, 1),
  (81, 1),
  (82, 1),
  (83, 1),
  (84, 1),
  (85, 2),
  (86, 4),
  (87, 1)

TF-IDF模型将向量从词袋表示（Bag-of-Words Representation）转换为向量空间，其中频率计数根据语料库中每个单词的相对稀有度（the relative rarity of each word in the corpus）进行加权。

In [24]:
from gensim import models
# 训练模型
tfidf = models.TfidfModel(bow_corpus,dictionary=dictionary)
# 对"知识图谱这种技术是企业转型的利器"进行转换
tfidf[dictionary.doc2bow("知识图谱 这种 技术 是 企业 转型 的 利器".split())]

[(233, 0.3888534988436588),
 (320, 0.34745151428336096),
 (413, 0.8060992821105257),
 (1356, 0.27977553331222366)]

TF-IDF模型再次返回元组列表，每个元组的第一个元素是词汇ID，第二个条目是TF-IDF加权值。 注意，对应于“知识图谱”的ID（在训练语料库中出现10次）
的加权值低于对应于“转型”的ID（在训练语料库中出现2次）权重值。

1. 生成字典 dictionary = corpora.Dictionary(train)
2. 生成语料 corpus = [dictionary.doc2bow(text) for text in train]
3. 定义TFIDF模型 tfidf_model = models.TfidfModel(corpus, dictionary=dictionary)
4. 用语料训练模型并生成TFIDF矩阵 corpus_tfidf = tfidf_model[corpus]
5. 生成余弦相似度索引 index = similarities.SparseMatrixSimilarity(corpus_tfidf, num_features=featurenum) 使用SparseMatrixSimilarity()，可以占用更少的内存和磁盘空间。

In [25]:
dictionary.save('../data/train_dictionary.dict')  # 保存生成的词典
tfidf.save('../data/train_tfidf.model')

In [28]:

corpus_tfidf = tfidf[bow_corpus]

## 计算相似度

In [29]:

from gensim import corpora,similarities,models

In [52]:
featurenum = len(dictionary.token2id.keys())  # 通过token2id得到特征数
# 稀疏矩阵相似度，从而建立索引,我们用待检索的文档向量初始化一个相似度计算的对象
index = similarities.SparseMatrixSimilarity(corpus_tfidf, num_features=featurenum)
index.save('../data/train_index.index')


- index.get_similarities(test_vec) 返回test_vec 和训练语料中所有文本的余弦相似度。返回结果是个numpy数组 
- related_doc_indices = sim.argsort()[:-6:-1] 完成对numpy数组的排序并获取其top5最大值。
 


In [50]:
dictionary = corpora.Dictionary.load("../data/train_dictionary.dict")
tfidf = models.TfidfModel.load("../data/train_tfidf.model")
index = similarities.SparseMatrixSimilarity.load('../data/train_index.index')
# item_id_list = joblib.load('item_id.pkl')
corpus = corpora.MmCorpus('../data/train_corpuse.mm')
print('模型加载完成')




模型加载完成


In [51]:
# 产生BOW向量
vec = dictionary.doc2bow(test)
#生成tfidf向量
test_vec = tfidf[vec]
# 计算相似度
sim = index.get_similarities(test_vec)
related_doc_indices = sim.argsort()[:-6:-1]
print(related_doc_indices)


[999 328 341 340 339]
